# Lab | API wrappers

In [41]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
import pandas as pd

In [42]:
# Create collection of song IDs and export to CSV.
    # 1. Get all the song IDs from several playlists.
    # 2. Get all the artist IDs from the song IDs.
    # 3. Get all the album IDs from the artist IDs.
    # 4. Get the song IDS from all the album IDs.

In [43]:
# Connect to Spotify's API

sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id,client_secret))

playlist_pop = sp.user_playlist_tracks("spotify", "64QxysD2w5x5EMLgcoT7fa")
playlist_indie = sp.user_playlist_tracks("spotify", "37i9dQZF1DX0lyZ45Ayi9S")
playlist_dance = sp.user_playlist_tracks("spotify", "33PyRULhtc4SRrUE1wbbmp")
playlist_rock = sp.user_playlist_tracks("spotify", "73wCNB78g3O2nIDLYJA35G")
playlist_electronic = sp.user_playlist_tracks("spotify", "0oXD7v9HUf2jFZXQfY2o4U")
playlist_chill = sp.user_playlist_tracks("spotify", "16gXsmg48MdRTqCLNnx9Cu")
playlist_metal = sp.user_playlist_tracks("spotify", "1yMlpNGEpIVUIilZlrbdS0")



playlists = {
    "pop": playlist_pop,
    "indie": playlist_indie,
    "dance": playlist_dance,
    "rock": playlist_rock,
    "electronic": playlist_electronic,
    "chill": playlist_chill,
    "metal": playlist_metal
}

playlists

{'pop': {'href': 'https://api.spotify.com/v1/playlists/64QxysD2w5x5EMLgcoT7fa/tracks?offset=0&limit=100&additional_types=track',
  'items': [{'added_at': '2023-01-27T06:04:14Z',
    'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/redmusiccompany'},
     'href': 'https://api.spotify.com/v1/users/redmusiccompany',
     'id': 'redmusiccompany',
     'type': 'user',
     'uri': 'spotify:user:redmusiccompany'},
    'is_local': False,
    'primary_color': None,
    'track': {'album': {'album_type': 'single',
      'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/716NhGYqD1jl2wI1Qkgq36'},
        'href': 'https://api.spotify.com/v1/artists/716NhGYqD1jl2wI1Qkgq36',
        'id': '716NhGYqD1jl2wI1Qkgq36',
        'name': 'Bizarrap',
        'type': 'artist',
        'uri': 'spotify:artist:716NhGYqD1jl2wI1Qkgq36'},
       {'external_urls': {'spotify': 'https://open.spotify.com/artist/0EmeFodog0BfCgMzAIvKQp'},
        'href': 'https://api.spotify

In [44]:
# 1. Get all the song IDs from a playlist

def get_song_ids(playlist):
    song_ids = []
    for track in playlist["items"]:
        song_ids.append(track["track"]["id"])
    return song_ids


In [45]:

all_song_ids = [song_id for playlist in playlists.values() for song_id in get_song_ids(playlist) ]
len(all_song_ids)

675

In [46]:
# 2. Get all the artist IDs from the playlist:

def get_artist_ids(playlist):
    artist_ids = set()
    for track in playlist["items"]:
        artist_id = track["track"]["artists"][0]['id']
        artist_ids.add(artist_id)
    return list(artist_ids)

In [47]:
all_artist_ids = [artist_id for playlist in playlists.values() for artist_id in get_artist_ids(playlist)]
len(all_artist_ids)


466

In [48]:
# 3. Get all the albums from the artist ids. 

def get_album_ids(artist_ids):
    album_ids = set()
    for artist_id in artist_ids:
        results = sp.artist_albums(artist_id, album_type='album')
        albums = results['items']
        for album in albums:
            album_ids.add(album['id'])
    return list(album_ids)


In [49]:
album_ids = get_album_ids(all_artist_ids)
len(album_ids)

3484

In [50]:
# 4. Get all the songs from the album ids
def all_songs(album_ids):
    all_songs = set()
    for album_id in album_ids:
        album_tracks = sp.album_tracks(album_id)
        tracks = album_tracks['items']
        for track in tracks:
            all_songs.add(track['id'])
            
    df = pd.DataFrame(all_songs, columns = {'song_ids'})
    df.to_csv('song_ids_final.csv', index='False')    
    return df       

In [51]:
df = all_songs(album_ids)

In [52]:
print(df.shape)
df.head(100)

(53682, 1)


song_ids
0   4EeVfvBfvS6b6PIiGYfmJj
1   7j5MFzkTeepzmGLowja8U7
2   5RWuUAmzl33AhtHJw8EhFD
3   7lzlXGt9Jipr5KK0QBVsMF
4   1wFQoEmwyRZj5F9OdTgemA
..                     ...
95  57bgzyZ9RL6DKLkF3HBDEK
96  3Dc7K91ASGGTTMhl77z95q
97  6IkOqHFLxbNwwgVv8QGl1A
98  0b2FdeskuwF5FcI3SH40Kq
99  7LdmWwc051HI5Y6O6P9GkK

[100 rows x 1 columns]

In [53]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53682 entries, 0 to 53681
Data columns (total 1 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   song_ids  53682 non-null  object
dtypes: object(1)
memory usage: 419.5+ KB
